In [22]:
from astropy.coordinates import SkyCoord
from ligo.skymap.io import fits
from ligo.skymap import plot
from ligo.skymap import postprocess
from astropy.time import Time
from astropy import units as u
import ligo.skymap.plot
import os
import json
from collections import defaultdict

import matplotlib
matplotlib.use('agg')
import matplotlib as mpl
from matplotlib import pyplot as plt

import numpy as np
fig_width_pt = 3*246.0  # Get this from LaTeX using \showthe\columnwidth
inches_per_pt = 1.0/72.27               # Convert pt to inch
golden_mean = (np.sqrt(5)-1.0)/2.0         # Aesthetic ratio
fig_width = fig_width_pt*inches_per_pt  # width in inches
fig_height = fig_width*golden_mean      # height in inches
fig_size =  [fig_width,fig_height]

params = { 'axes.labelsize': 24,
          'font.family': 'serif',
          'font.serif': 'Computer Modern Raman',
          'font.size': 24,
          'legend.fontsize': 20,
          'xtick.labelsize': 24,
          'ytick.labelsize': 24,
          'text.usetex': True,
          'lines.markersize' : 14,
          'figure.figsize': fig_size}

mpl.rcParams.update(params)

"""
Plot skymaps for O1 & O2 catalog events.
"""

def make_skymaps(fits_dict, event_colors, filename, gpstime,
                 contour_lvl=(50, 90), dpi=300, geo=True, label=True,
                 label_dicts=[dict(), dict()]):
    #fig = plt.figure(figsize=(4, 4), dpi=dpi)
    fig = plt.figure()
    # Set time
    ax = plt.axes(projection=('geo degrees mollweide' if geo
                              else 'astro hours mollweide'),
                  obstime=Time(gpstime, format='gps').utc.isot)

    # Plot contours
    for event, fits_file in fits_dict.items():
        color = event_colors[event]
        skymap, metadata = fits.read_sky_map(fits_file, nest=None)
        cls = 100 * postprocess.find_greedy_credible_levels(skymap)
        cs = ax.contour_hpx(
            (cls, 'ICRS'), nested=metadata['nest'],
            colors=color, linewidths=1, levels=contour_lvl)

        if label:
            # Set labels manually
            manual_labels, label_rotations = label_dicts
            for loc, rot in zip(manual_labels[event], label_rotations[event]):
                plt.text(loc[0], loc[1], event, fontsize=24, color=color, rotation=rot)

    ax.grid()

    if geo:
        # Add continents.
        geojson_filename = os.path.join(
            os.path.dirname(plot.__file__), 'ne_simplified_coastline.json')
        with open(geojson_filename, 'r') as geojson_file:
            geoms = json.load(geojson_file)['geometries']
        verts = [coord for geom in geoms
            for coord in zip(*geom['coordinates'])]
        plt.plot(*verts, color='0.5', linewidth=0.5,
            transform=ax.get_transform('world'))


    plt.savefig(filename+'.pdf')
    plt.savefig(filename+'.png')
    plt.close()

In [28]:
from pycbc.inference import io
#------------------------------------------------------------------------------
if __name__ == "__main__":

    
    fits_dict = defaultdict(str,
                {'200205_201716': '/work/yifan.wang/grb/gwrun/skymap_test/200205_201716.fits',
                 'GRB 200205845': '/work/yifan.wang/grb/git-notebooks/make_grb_background/fermi_lgrb_fits/glg_healpix_all_bn200205845_v00.fit',})

    event_colors = defaultdict(str,
                {'200205_201716': 'tab:blue',#'#00a7f0',
                 'GRB 200205845': 'tab:green'})#'#00b1a4'})

    # These labels are for dpi=600
    manual_labels = { 
      '200205_201716': [(405, 260)],
      'GRB 200205845': [(205, 25)],

    }

    label_rotations = {
      '200205_201716': [0],
      'GRB 200205845': [0]
    }

    #mpl.rcParams['font.size'] = 12

    events_all = set(fits_dict.keys())
    fits_dict = {k:fits_dict[k] for k in events_all}
    
    gw=io.loadfile('/work/yifan.wang/grb/gwrun/o3b/result/200205_201716.hdf','r')
    config = gw.read_config_file()
    gpstime = config.get('trigger', 'trigger_time')
    
    # plot events split into two sets in two plots
    make_skymaps(fits_dict, event_colors, 'GWlong-GRB', gpstime,
                     contour_lvl=(50.0, 90.0), dpi=600, geo=False, label=True,
                     label_dicts=[manual_labels, label_rotations])